In [39]:
import pandas as pd
import numpy as np
import difflib
import geojson
from pymongo import MongoClient

client = MongoClient()
db = client.studio
collection_airbnb_madrid = db.airbnb_madrid
data_airbnb_madrid = pd.DataFrame(list(collection_airbnb_madrid.find()))

collction_airbnb_barcelona = db.airbnb_barcelona
data_airbnb_barcelona = pd.DataFrame(list(collction_airbnb_barcelona.find()))

collection_buy_madrid = db.buy_madrid
data_buy_madrid = pd.DataFrame(list(collection_buy_madrid.find()))

collection_buy_barcelona = db.buy_barcelona
data_buy_barcelona = pd.DataFrame(list(collection_buy_barcelona.find()))

collection_rent_madrid = db.rent_madrid
data_rent_madrid = pd.DataFrame(list(collection_rent_madrid.find()))

collection_rent_barcelona = db.rent_barcelona
data_rent_barcelona = pd.DataFrame(list(collection_rent_barcelona.find()))

data_buy_madrid.dropna(inplace=True)
data_buy_barcelona.dropna(inplace=True)

data_rent_madrid.dropna(inplace=True)
data_rent_madrid.dropna(inplace=True)

In [40]:
import plotly.express as px
# The initial datasets will probably contain a lot of erroneous values and outliers. We need to check this
# before filtering them
fig = px.box(data_buy_madrid, y="price")
fig.show()

fig = px.box(data_buy_madrid, y="surface")
fig.show()

fig = px.box(data_buy_barcelona, y="price")
fig.show()

fig = px.box(data_buy_barcelona, y="surface")
fig.show()

fig = px.box(data_rent_madrid, y="price")
fig.show()

fig = px.box(data_rent_madrid, y="surface")
fig.show()

fig = px.box(data_rent_barcelona, y="price")
fig.show()

fig = px.box(data_rent_barcelona, y="surface")
fig.show()

In [41]:
print(data_buy_barcelona.describe())
print(data_buy_madrid.describe())
print(data_rent_barcelona.describe())
print(data_rent_madrid.describe())

            toilets         price         rooms        surface
count  2.108900e+04  2.108900e+04  21089.000000   21089.000000
mean   2.430420e+02  3.400792e+05      3.460856     293.510598
std    1.283354e+04  4.365234e+05      1.383568    9460.028088
min    1.000000e+00  6.696000e+03      1.000000       1.000000
25%    2.000000e+00  1.550000e+05      3.000000      80.000000
50%    7.000000e+00  2.300000e+05      3.000000     105.000000
75%    2.500000e+01  3.640000e+05      4.000000     181.000000
max    1.300000e+06  1.500000e+07     42.000000  900000.000000
            toilets         price         rooms       surface
count  15191.000000  1.519100e+04  15191.000000  1.519100e+04
mean      12.238628  4.659958e+05      3.107498  3.988068e+02
std      160.998734  6.443195e+05      1.460371  1.925912e+04
min        1.000000  1.490000e+02      1.000000  1.000000e+00
25%        1.000000  1.475000e+05      2.000000  7.200000e+01
50%        2.000000  2.470000e+05      3.000000  1.000000e+02

#### Data filtering
Once we know that our datasets contain a lot of wrong values and outliers we need to get rid of them so we can work with it.

In [42]:
buy_madrid_prefilter = data_buy_madrid["_id"].count()
# We start by deleting extreme irrational cases
data_buy_madrid = data_buy_madrid[(data_buy_madrid.surface < 1500) & (data_buy_madrid.surface > 10) & (data_buy_madrid.price > 10000)  & (data_buy_madrid.toilets < 10)]
# Done that, we filter for other possible outliers
data_buy_madrid = data_buy_madrid[np.abs(data_buy_madrid.price-data_buy_madrid.price.mean())<=(3*data_buy_madrid.price.std())]
print("Filtered values for: properties for sale Madrid")
print(buy_madrid_prefilter - data_buy_madrid["_id"].count())

buy_barcelona_prefilter = data_buy_barcelona["_id"].count()
data_buy_barcelona = data_buy_barcelona[(data_buy_barcelona.surface < 1500) & (data_buy_barcelona.surface > 10) & (data_buy_barcelona.price > 10000) & (data_buy_barcelona.toilets < 10)]
data_buy_barcelona = data_buy_barcelona[np.abs(data_buy_barcelona.price-data_buy_barcelona.price.mean())<=(3*data_buy_barcelona.price.std())]
print("Filtered values for: properties for sale Barcelona")
print(buy_barcelona_prefilter - data_buy_barcelona["_id"].count())


rent_madrid_prefilter = data_rent_madrid["_id"].count()
data_rent_madrid = data_rent_madrid[(data_rent_madrid.surface < 1500) & (data_rent_madrid.surface > 10) & (data_rent_madrid.price > 100) & (data_rent_madrid.toilets < 10)]
data_rent_madrid = data_rent_madrid[np.abs(data_rent_madrid.price-data_rent_madrid.price.mean())<=(3*data_rent_madrid.price.std())]
print("Filtered values for: properties for rent Madrid")
print(rent_madrid_prefilter - data_rent_madrid["_id"].count())

rent_barcelona_prefilter = data_rent_barcelona["_id"].count()
data_rent_barcelona = data_rent_barcelona[(data_rent_barcelona.surface < 1500) & (data_rent_barcelona.surface > 10) & (data_rent_barcelona.price > 100) & (data_rent_barcelona.toilets < 10)]
data_rent_barcelona = data_rent_barcelona[np.abs(data_rent_barcelona.price-data_rent_barcelona.price.mean())<=(3*data_rent_barcelona.price.std())]
print("Filtered values for: properties for rent Barcelona")
print(rent_barcelona_prefilter - data_rent_barcelona["_id"].count())

Filtered values for: properties for sale Madrid
976
Filtered values for: properties for sale Barcelona
9993
Filtered values for: properties for rent Madrid
164
Filtered values for: properties for rent Barcelona
5687


In [43]:
# We filter the price column to get it from string to float
data_airbnb_madrid["price"] = data_airbnb_madrid['price'].str.replace('$','').str.replace(',','')
data_airbnb_madrid["price"] = data_airbnb_madrid["price"].astype(float)

data_airbnb_barcelona["price"] = data_airbnb_barcelona['price'].str.replace('$','').str.replace(',','')
data_airbnb_barcelona["price"] = data_airbnb_barcelona["price"].astype(float)

#### Geographic adaptation

As we'll need to work with geo-operations comparing our airbnb and habitaclia datasets we need to standarize the geographic information so we can correlate data between those two datasets.

In [44]:
# Scrapped data includes "Zona" as it is added by habitaclia. We remove that string for a better standarization
# with airbnb "neighbourhood" column. 
# At the end we want to have a column to join habitaclia data with the airbnb dataset

def make_geojson_coords(x):
    coords_obj = {"type": "Point", "coordinates": [x['longitude'],x['latitude']]}
    return coords_obj

def get_neighbourhood_airbnb(x,s):
    if x["area"]:
        area = x["area"]
        detected_area = difflib.get_close_matches(area, s)
        if detected_area:
            return detected_area[0]
        else:
            return None
    else:
        return None

def unfold_coords(x, coord):
    try:
        if x["coords"]:
            if coord == "lat":
                lat = x["coords"]["coordinates"][1]
                return lat
            if coord == "lon":
                lon = x["coords"]["coordinates"][0]
                return lon
        else:
            return None
    except:
        return None


data_buy_madrid["area"] = data_buy_madrid['area'].str.replace('Zona ','')
# Images and features are lists. We'll generate a couple of columns so we can work with their lenght
data_buy_madrid["images_len"] = data_buy_madrid['images'].str.len()
data_buy_madrid["features_len"] = data_buy_madrid['feats'].str.len()

data_rent_madrid["area"] = data_rent_madrid['area'].str.replace('Zona ','')
data_rent_madrid["images_len"] = data_rent_madrid['images'].str.len()
data_rent_madrid["features_len"] = data_rent_madrid['feats'].str.len()

data_buy_barcelona["area"] = data_buy_barcelona["area"].str.replace('Zona ','')
data_buy_barcelona["images_len"] = data_buy_barcelona['images'].str.len()
data_buy_barcelona["features_len"] = data_buy_barcelona['feats'].str.len()

data_rent_barcelona["area"] = data_rent_barcelona["area"].str.replace('Zona ','')
data_rent_barcelona["images_len"] = data_rent_barcelona['images'].str.len()
data_rent_barcelona["features_len"] = data_rent_barcelona['feats'].str.len()


# neighbourhood_barcelona / madrid were downloaded form the insideairbnb site
with open("neighbourhood_barcelona.geojson") as geo_barcelona:
    gj_barcelona = geojson.load(geo_barcelona)
features_barcelona = gj_barcelona['features']

with open("neighbourhood_madrid.geojson") as geo_madrid:
    gj_madrid = geojson.load(geo_madrid)
features_madrid = gj_madrid['features']

# we'll extract all the unique neighbourhoods from those datasets
set_madrid = set( val for dic in features_madrid for val in dic["properties"].values())
set_barcelona = set( val for dic in features_barcelona for val in dic["properties"].values())

# and then relate them to the filtered "area" column in our datasets from habitaclia
data_buy_madrid["neighbourhood"] = data_buy_madrid.apply((lambda x: get_neighbourhood_airbnb(x,set_madrid)), axis=1)
data_rent_madrid["neighbourhood"] = data_buy_madrid.apply((lambda x: get_neighbourhood_airbnb(x, set_madrid)), axis=1)

data_buy_barcelona["neighbourhood"] = data_buy_barcelona.apply((lambda x: get_neighbourhood_airbnb(x,set_barcelona)), axis=1)
data_rent_barcelona["neighbourhood"] = data_buy_barcelona.apply((lambda x: get_neighbourhood_airbnb(x, set_barcelona)), axis=1)

# Mapbox maps in plotly are very picky
# they need lat and lon columns not geojson. But we'll need both, lat/lon for plot and geojson
# for the custom choropleths and other geo operations.
# We unfold the geojson point into lat/lon for easy processing with plotly mapbox maps
data_buy_madrid['lat'] = data_buy_madrid.apply((lambda x: unfold_coords(x,'lat')), axis=1)
data_buy_madrid['lon'] = data_buy_madrid.apply((lambda x: unfold_coords(x,'lon')), axis=1)

data_buy_barcelona['lat'] = data_buy_barcelona.apply((lambda x: unfold_coords(x,'lat')), axis=1)
data_buy_barcelona['lon'] = data_buy_barcelona.apply((lambda x: unfold_coords(x,'lon')), axis=1)

data_rent_madrid['lat'] = data_rent_madrid.apply((lambda x: unfold_coords(x,'lat')), axis=1)
data_rent_madrid['lon'] = data_rent_madrid.apply((lambda x: unfold_coords(x,'lon')), axis=1)

data_rent_barcelona['lat'] = data_rent_barcelona.apply((lambda x: unfold_coords(x,'lat')), axis=1)
data_rent_barcelona['lon'] = data_rent_barcelona.apply((lambda x: unfold_coords(x,'lon')), axis=1)

# for the same reason we'll also need the coords in the airbnb dataset to be in geojson as well
data_airbnb_madrid["coords"] = data_airbnb_madrid.apply(make_geojson_coords, axis=1)
data_airbnb_barcelona["coords"] = data_airbnb_barcelona.apply(make_geojson_coords, axis=1)

#### Feature selection and one hot encoding

The *feats* column contains a list of features for each row. Those features are manually entered by the user, so the values may vary a lot also containing a lot of redundant information. We'll analyse the datasets then select the most interesting features and encode them by using one hot encoding, so we can work with them when analysing the data.

In [45]:
unique_feats = (data_buy_madrid["feats"].explode().unique())

print(unique_feats.tolist())

['2 habitaciones', 'Superficie 74\xa0m', '1 Baño', 'Cocina tipo office ', 'Lavadero ', 'Trastero ', 'Calefacción ', '\r\n                    ', '\r\nEn trámite                   \r\n                ', 'Ascensor ', '3 habitaciones', 'Superficie 130\xa0m', '2 Baños', 'Plaza parking ', 'Año construcción 1970', 'Jardín comunitario ', '4 habitaciones', 'Superficie 132\xa0m', 'Cuota comunidad 130€ ', '5 habitaciones', 'Superficie 289\xa0m', '3 Baños', '1 Aseo', 'Aire acondicionado ', 'Año construcción 2000', 'Vistas a la montaña ', 'Equipamiento deportivo ', 'Superficie 210\xa0m', '4 Baños', 'Despacho ', 'Cocina tipo office: No', 'Estado cocina: buen estado', 'Sin plaza parking', 'Año construcción 1983', 'Cerca de transporte público ', '\r\n                        ', '\r\n                   \r\n                ', 'Cuota comunidad 210€ ', 'Superficie 224\xa0m', 'Sin aire acondicionado', 'Piscina comunitaria ', 'Superficie 120\xa0m', 'Estado cocina: bueno', 'Planta número 1', 'Año construcción

In [46]:
# As we have a lot of rendudant/unclean feats, we select the ones we are interested in and we code them into
# the dataset by using a custom one-hot encoding
# feats:  'Aire acondicionado ', 'Amueblado ', 'Ascensor ', 'Chimenea ', 'Cerca de transporte público ', 
# 'Equipamiento deportivo ', 'Obra nueva ', 'Jardín comunitario ', 'Piscina comunitaria ', 'Piscina propia '
# 'Trastero ', 'Vistas a la ciudad ', 'Vistas a la montaña ', 'Vigilancia ', 'Plaza parking '
def encode_key_feats(x,feat):
    if feat == "air_conditioning":
        if 'Aire acondicionado ' in x["feats"]:
            return 1
        else:
            return 0
    if feat == "furniture":
        if 'Amueblado ' in x["feats"]:
            return 1
        else:
            return 0
    if feat == "elevator":
        if 'Ascensor ' in x["feats"]:
            return 1
        else:
            return 0
    if feat == "chimney":
        if 'Chimenea ' in x["feats"]:
            return 1
        else:
            return 0
    if feat == "public_transport":
        if 'Cerca de transporte público ' in x["feats"]:
            return 1
        else:
            return 0
    if feat == "sports":
        if 'Equipamiento deportivo ' in x["feats"]:
            return 1
        else:
            return 0
    if feat == "new_construction":
        if 'Obra nueva ' in x["feats"]:
            return 1
        else:
            return 0
    if feat == "garden_community":
        if 'Jardín comunitario ' in x["feats"]:
            return 1
        else:
            return 0
    if feat == "pool_community":
        if 'Piscina comunitaria ' in x["feats"]:
            return 1
        else:
            return 0
    if feat == "pool":
        if 'Piscina propia ' in x["feats"]:
            return 1
        else:
            return 0
    if feat == "storage":
        if 'Trastero ' in x["feats"]:
            return 1
        else:
            return 0
    if feat == "views_city":
        if 'Vistas a la ciudad ' in x["feats"]:
            return 1
        else:
            return 0
    if feat == "views_mountain":
        if 'Vistas a la montaña ' in x["feats"]:
            return 1
        else:
            return 0
    if feat == "security":
        if 'Vigilancia ' in x["feats"]:
            return 1
        else:
            return 0
    if feat == "parking":
        if 'Plaza parking ' in x["feats"]:
            return 1
        else:
            return 0
        
def encode_features(dataset):
    features = ["parking", "security", "views_mountain", "views_city", "storage", "pool", "pool_community",
               "garden_community", "new_construction", "sports", "public_transport", "chimney", "chimney",
               "elevator", "air_conditioning"]

    for f in features:
        dataset[f] = dataset.apply((lambda x: encode_key_feats(x,f)), axis=1)
    
    return dataset

        

data_buy_madrid = encode_features(data_buy_madrid)
data_buy_barcelona = encode_features(data_buy_barcelona)
data_rent_madrid = encode_features(data_rent_madrid)
data_rent_barcelona = encode_features(data_rent_barcelona)

#### Data check after the filtering

Once we have filtered the dataset as well as added some new useful columns we can re-check our data to see if it now makes more sense according to our analysis requisites.

In [48]:
fig = px.box(data_buy_madrid, y="price")
fig.show()

fig = px.box(data_buy_madrid, y="surface")
fig.show()

fig = px.box(data_buy_barcelona, y="price")
fig.show()

fig = px.box(data_buy_barcelona, y="surface")
fig.show()

fig = px.box(data_rent_madrid, y="price")
fig.show()

fig = px.box(data_rent_madrid, y="surface")
fig.show()

fig = px.box(data_rent_barcelona, y="price")
fig.show()

fig = px.box(data_rent_barcelona, y="surface")
fig.show()

In [47]:
print(data_buy_barcelona.describe())
print(data_buy_madrid.describe())
print(data_rent_barcelona.describe())
print(data_rent_madrid.describe())

            toilets         price         rooms       surface    images_len  \
count  11096.000000  1.109600e+04  11096.000000  11096.000000  11096.000000   
mean       2.477379  2.362676e+05      3.186644    122.110400     20.970260   
std        1.986895  1.707846e+05      1.081970     94.052618     12.977487   
min        1.000000  1.520000e+04      1.000000     16.000000      0.000000   
25%        1.000000  1.350000e+05      3.000000     75.000000     12.000000   
50%        2.000000  1.880000e+05      3.000000     91.000000     19.000000   
75%        3.000000  2.750000e+05      4.000000    126.000000     27.000000   
max        9.000000  1.245000e+06     18.000000   1357.000000    124.000000   

       features_len           lat           lon       parking      security  \
count  11096.000000  11096.000000  11096.000000  11096.000000  11096.000000   
mean      13.396179     40.024660      0.776846      0.290014      0.018745   
std        4.977411      8.788017     14.141534    